# Module 05 Project Overview

The purpose of this project is to examine the 

In [1]:
import pandas as pd
import numpy as np
import pandas_profiling

In [94]:
raw_df = pd.read_csv("diabetes_data.csv")
df = pd.read_csv("diabetes_data.csv")

In [4]:
df.head()

encounter_id  patient_nbr             race  gender      age weight  \
0       2278392      8222157        Caucasian  Female   [0-10)      ?   
1        149190     55629189        Caucasian  Female  [10-20)      ?   
2         64410     86047875  AfricanAmerican  Female  [20-30)      ?   
3        500364     82442376        Caucasian    Male  [30-40)      ?   
4         16680     42519267        Caucasian    Male  [40-50)      ?   

   admission_type_id  discharge_disposition_id  admission_source_id  \
0                  6                        25                    1   
1                  1                         1                    7   
2                  1                         1                    7   
3                  1                         1                    7   
4                  1                         1                    7   

   time_in_hospital    ...     citoglipton insulin  glyburide-metformin  \
0                 1    ...              No      No                   No   
1                 3    ...              No      Up                   No   
2                 2    ...              No      No                   No   
3                 2    ...              No      Up                   No   
4                 1    ...              No  Steady                   No   

   glipizide-metformin  glimepiride-pioglitazone  metformin-rosiglitazone  \
0                   No                        No                       No   
1                   No                        No                       No   
2                   No                        No                       No   
3                   No                        No                       No   
4                   No                        No                       No   

   metformin-pioglitazone  change diabetesMed readmitted  
0                      No      No          No         NO  
1                      No      Ch         Yes        >30  
2                      No      No         Yes         NO  
3                      No      Ch         Yes         NO  
4                      No      Ch         Yes         NO  

[5 rows x 50 columns]

In [5]:
len(df)

101766

In [6]:
df.profile_report()

## Preprocessing

In [7]:
df.head()

encounter_id  patient_nbr             race  gender      age weight  \
0       2278392      8222157        Caucasian  Female   [0-10)      ?   
1        149190     55629189        Caucasian  Female  [10-20)      ?   
2         64410     86047875  AfricanAmerican  Female  [20-30)      ?   
3        500364     82442376        Caucasian    Male  [30-40)      ?   
4         16680     42519267        Caucasian    Male  [40-50)      ?   

   admission_type_id  discharge_disposition_id  admission_source_id  \
0                  6                        25                    1   
1                  1                         1                    7   
2                  1                         1                    7   
3                  1                         1                    7   
4                  1                         1                    7   

   time_in_hospital    ...     citoglipton insulin  glyburide-metformin  \
0                 1    ...              No      No                   No   
1                 3    ...              No      Up                   No   
2                 2    ...              No      No                   No   
3                 2    ...              No      Up                   No   
4                 1    ...              No  Steady                   No   

   glipizide-metformin  glimepiride-pioglitazone  metformin-rosiglitazone  \
0                   No                        No                       No   
1                   No                        No                       No   
2                   No                        No                       No   
3                   No                        No                       No   
4                   No                        No                       No   

   metformin-pioglitazone  change diabetesMed readmitted  
0                      No      No          No         NO  
1                      No      Ch         Yes        >30  
2                      No      No         Yes         NO  
3                      No      Ch         Yes         NO  
4                      No      Ch         Yes         NO  

[5 rows x 50 columns]

In [95]:
df = df.drop('weight', axis=1) #Dropping weight since too few rows have actual values
df = df.drop('payer_code', axis=1) #Unnecessary for classification task
df = df.drop('citoglipton', axis=1) #Rejected
df = df.drop('examide', axis=1) #Rejected

Because the medical specialty of the service provider could have influence on whether the H1bAlc test was performed, missing values will be replace with 'Unknown'.

In [96]:
df['medical_specialty'].replace(to_replace='?', value='Unknown', inplace=True)

In [97]:
df.race.value_counts(normalize=True)

Caucasian          0.747784
AfricanAmerican    0.188766
?                  0.022336
Hispanic           0.020017
Other              0.014799
Asian              0.006299
Name: race, dtype: float64

The following code replaces missing values in the race column with a random choice aligned with the probabilities of all other race options.

In [98]:
df['race'] = df['race'].apply(lambda x: np.random.choice(['Caucasian', 'AfricanAmerican','Hispanic', 'Other', 'Asian'], p=[0.76, 0.19, 0.02, 0.02, 0.01]) if x == '?' else x)

In [99]:
df.race.value_counts(normalize=True) #Confirming appropriate distribution

Caucasian          0.765118
AfricanAmerican    0.192854
Hispanic           0.020449
Other              0.015113
Asian              0.006466
Name: race, dtype: float64

In [100]:
df.gender.value_counts()

Female             54708
Male               47055
Unknown/Invalid        3
Name: gender, dtype: int64

In [101]:
df = df[df.gender != 'Unknown/Invalid']

In [102]:
df.admission_type_id.value_counts()

1    53988
3    18868
2    18480
6     5291
5     4785
8      320
7       21
4       10
Name: admission_type_id, dtype: int64

In [103]:
for col in df.columns:
    print(col, df[col].unique(), '\n\n')

encounter_id [  2278392    149190     64410 ... 443854148 443857166 443867222] 


patient_nbr [  8222157  55629189  86047875 ... 140199494 120975314 175429310] 


race ['Caucasian' 'AfricanAmerican' 'Hispanic' 'Other' 'Asian'] 


gender ['Female' 'Male'] 


age ['[0-10)' '[10-20)' '[20-30)' '[30-40)' '[40-50)' '[50-60)' '[60-70)'
 '[70-80)' '[80-90)' '[90-100)'] 


admission_type_id [6 1 2 3 4 5 8 7] 


discharge_disposition_id [25  1  3  6  2  5 11  7 10  4 14 18  8 13 12 16 17 22 23  9 20 15 24 28
 19 27] 


admission_source_id [ 1  7  2  4  5  6 20  3 17  8  9 14 10 22 11 25 13] 


time_in_hospital [ 1  3  2  4  5 13 12  9  7 10  6 11  8 14] 


medical_specialty ['Pediatrics-Endocrinology' 'Unknown' 'InternalMedicine'
 'Family/GeneralPractice' 'Cardiology' 'Surgery-General' 'Orthopedics'
 'Gastroenterology' 'Surgery-Cardiovascular/Thoracic' 'Nephrology'
 'Orthopedics-Reconstructive' 'Psychiatry' 'Emergency/Trauma'
 'Pulmonology' 'Surgery-Neuro' 'Obsterics&Gynecology-GynecologicOnco'

number_diagnoses [ 1  9  6  7  5  8  3  4  2 16 12 13 15 10 11 14] 


max_glu_serum ['None' '>300' 'Norm' '>200'] 


A1Cresult ['None' '>7' '>8' 'Norm'] 


metformin ['No' 'Steady' 'Up' 'Down'] 


repaglinide ['No' 'Up' 'Steady' 'Down'] 


nateglinide ['No' 'Steady' 'Down' 'Up'] 


chlorpropamide ['No' 'Steady' 'Down' 'Up'] 


glimepiride ['No' 'Steady' 'Down' 'Up'] 


acetohexamide ['No' 'Steady'] 


glipizide ['No' 'Steady' 'Up' 'Down'] 


glyburide ['No' 'Steady' 'Up' 'Down'] 


tolbutamide ['No' 'Steady'] 


pioglitazone ['No' 'Steady' 'Up' 'Down'] 


rosiglitazone ['No' 'Steady' 'Up' 'Down'] 


acarbose ['No' 'Steady' 'Up' 'Down'] 


miglitol ['No' 'Steady' 'Down' 'Up'] 


troglitazone ['No' 'Steady'] 


tolazamide ['No' 'Steady' 'Up'] 


insulin ['No' 'Up' 'Steady' 'Down'] 


glyburide-metformin ['No' 'Steady' 'Down' 'Up'] 


glipizide-metformin ['No' 'Steady'] 


glimepiride-pioglitazone ['No' 'Steady'] 


metformin-rosiglitazone ['No' 'Steady'] 


metformin-pioglitazone ['No' '

In [93]:
df.discharge_disposition_id.value_counts()

1     60232
3     13954
6     12902
18     3691
2      2128
22     1992
11     1642
5      1184
25      989
4       815
7       623
23      412
13      399
14      372
28      139
8       108
15       63
24       48
9        21
17       14
16       11
19        8
10        6
27        5
12        3
20        2
Name: discharge_disposition_id, dtype: int64